Я вижу два решения:

Для простоты я бы сделал 2 класса датасета
Если нужно кодировать лишь последовательность букв, он и хранит последовательности букв сразу и не хранит коордианты

В обоих случаях декодер оперирует эмбеддингами букв текста

<h3>1. На вход энкодера x, y, t, dx/dt, dy/st, x'', y'', keybard_key_embedding</h3>

**Что делать, если ближайшая клавиша неалфавитная (пунктуация, клавиши-действия)?**

Добавлю для всех неалфавитных клавиш один специальный токен. Хотя, возможно,
лучше добавить отдельный токен для каждой клавиши. Кажется, в кавиатуре схожесть
клавиш определяется тем, насколько часто они встречаются рядом друг с другом.
Тогда может быть важно отличать enter, который близок к бкве `э`, например,
от `caps lock`, который близок к `ф`. Отмечу, что схожесть в данном случае - это
не просто физическое расстояние между клавишами (хотя отчасти и так), но скорее, похожесть
клавиш `a` и `b` означает, что для последовательностей вида `letter1`, `letter2` ... `letterX`, `letterN`
если вероятность, что `letterX` = `a` велика, то вероятность, что `letterX` = `b` тоже велика.


**Где происходит инициализация токенизатора?**
я бы вынес токенезатор вне датасета и передавал бы его в конструктор датасета.


для каждой раскладки свои instance'ы датасета и модели.



<h3> 2. На вход энкодера последовательность клавиш клавиатуры </h3>

Если ближайшая клавиша неалфавитная **пропускать**

**Где происходит инициализация токенизатора?**


один instance датасета и одна модель для всех раскладок.


Реализовывать ли для каждого варианта отдельный токенизатор:

У нас может быть различное количество токенов: в некотоорых раскладках отсутствует символ "ъ", например

Когда датасет содержит лишь одну раскладку, токенизатор должен учесть символы из одной раскладки. Когда датасет содержит несколько раскладок, токенизатор должен учесть символы из всех раскладок.

Кажется, что варьируется только наличие 'ъ' и 'ё'. Во-первых, не ясно нужны ли эти символы. Есть желание заменять 'ё' на 'е', а 'ъ' на 'ь'. 

Кажется, нас совершенно устраивает токенизатор, содержащий все буквы русского языка, включая 'ё' и 'ъ'. Наличие пары лишних токенов незначительно увеличит размер эмбеддинг-матрицы, но не повлияет на обучение модели.

In [7]:
import os

import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader, IterableDataset

# from model import SwipeCurveEncoderTransformer

In [17]:
data_root = os.path.normpath("../data/data_separated_grid")

In [18]:
from typing import List, Optional

class CharLevelTokenizerv1:
    """
    Tokenizes a word into a list of integers.

    Toknized word is padded to the max_word_len.

    Guarantees that <sos> and <pad> are tokens with `vocab_len - 1`
    and `vocab_len - 2` indices respectively.
    This is useful because model never generates <sos> and <pad> tokens.
    """
    def __init__(self, vocab_path):
        self.char_to_idx = {}
        self.idx_to_char = {}
        self.max_word_len = None  # is set in _build_vocab
        self._build_vocab(vocab_path)

    def _build_vocab(self, vocab_path):
        self.max_word_len = 0
        special_tokens = ["<eos>", "<pad>", "<unk>", "<sos>"]
        unique_chars = set()

        with open(vocab_path, "r", encoding="utf-8") as f:
            vocab = f.read().split("\n")
            for word in vocab:
                self.max_word_len = max(self.max_word_len, len(word) + 2)  # + <sos> and <eos>
                for char in word:
                    unique_chars.add(char)
                    
        unique_chars_list = sorted(list(unique_chars)) + special_tokens
        self.char_to_idx = {char: idx for idx, char in enumerate(unique_chars_list)}
        self.idx_to_char = {idx: char for idx, char in enumerate(unique_chars_list)}

    def _tokenize_word(self, word):
        """
        Tokenizes a word into a list of integers.
        """
        tokenized_word = []
        tokenized_word.append(self.char_to_idx["<sos>"])
        for char in word:
            default: int = self.char_to_idx['<unk>']
            tokenized_word.append(self.char_to_idx.get(char, default))
        tokenized_word.append(self.char_to_idx["<eos>"])
        return tokenized_word
    
    
    def _pad(self, tokenized_word):
        """
        Pads a word to the max_word_len.
        """
        return tokenized_word + [self.char_to_idx["<pad>"]] * (self.max_word_len - len(tokenized_word))
    
    def tokenize(self, word):
        """
        Tokenizes a word and pads it to the max_word_len.
        """
        token_seq = torch.tensor(self._pad(self._tokenize_word(word)))
        mask = torch.ones(self.max_word_len, dtype=torch.bool)
        mask[:len(word)+2] = False
        return token_seq, mask
    
    def decode(self, token_seq):
        """
        Decodes a tokenized word into a string.
        """
        return "".join([self.idx_to_char[int(idx)] for idx in token_seq])

In [19]:
import pickle

word_tokenizer = CharLevelTokenizerv1(os.path.join(data_root, "voc.txt"))

word_tokenizer_save_path = "../data/data_separated_grid/word_tokenizer.pkl"

with open(word_tokenizer_save_path, 'wb') as f:
    pickle.dump(word_tokenizer, f, protocol=pickle.HIGHEST_PROTOCOL)

with open(word_tokenizer_save_path, 'rb') as f:
    word_tokenizer = pickle.load(f)

In [20]:
print(word_tokenizer.idx_to_char)

{0: '-', 1: 'а', 2: 'б', 3: 'в', 4: 'г', 5: 'д', 6: 'е', 7: 'ж', 8: 'з', 9: 'и', 10: 'й', 11: 'к', 12: 'л', 13: 'м', 14: 'н', 15: 'о', 16: 'п', 17: 'р', 18: 'с', 19: 'т', 20: 'у', 21: 'ф', 22: 'х', 23: 'ц', 24: 'ч', 25: 'ш', 26: 'щ', 27: 'ъ', 28: 'ы', 29: 'ь', 30: 'э', 31: 'ю', 32: 'я', 33: '<eos>', 34: '<pad>', 35: '<unk>', 36: '<sos>'}


In [21]:
class KeyboardTokenizerv1:
    
    i2t = ['а', 'б', 'в', 'г', 'д', 'е', 'ë', 'ж', 'з', 'и', 'й',
           'к', 'л', 'м', 'н', 'о', 'п', 'р', 'с', 'т', 'у', 'ф',
           'х', 'ц', 'ч', 'ш', 'щ', 'ъ', 'ы', 'ь', 'э', 'ю', 'я',
           '-', '<unk>', '<pad>']
    
    t2i = {t: i for i, t in enumerate(i2t)}

    def get_token(self, char):
        return self.t2i.get(char, self.t2i['<unk>'])

In [22]:
import json
from typing import Optional, List, Tuple, Dict
import array
import numpy as np

import torch
from torch.utils.data import Dataset
from tqdm import tqdm


class NeuroSwipeDatasetv1(Dataset):
    """
    Dataset class for NeuroSwipe dataset.
    The dataset file weights over 3 GB and contains over 6 million swipe gestures.
    """

    def __init__(self,
                 data_path: str,
                 gridname_to_grid: dict,
                 kb_tokenizer: KeyboardTokenizerv1,
                 max_traj_len: int,
                 word_tokenizer: CharLevelTokenizerv1,  # should contain max word len
                 include_time: bool = False,
                 include_velocities: bool = True,
                 include_accelerations: bool = True,
                 include_grid_name: bool = False,
                 has_target = True,
                 has_one_grid_only = True,
                 total: Optional[int] = None):
        """
        Argsuments:
        -----------
        data_path (string): Path to the NeuroSwipe dataset in JSON format.
            A custom version of the dataset is used:
            "grid" property is replaced with "grid_name" property.
        """
        if include_accelerations and not include_velocities:
            raise ValueError("Accelerations are supposed \
                             to be an addition to velocities. Add velocities.")
        
        if has_one_grid_only and len(gridname_to_grid) != 1:
            raise ValueError(f"has_one_grid_only is True \
                             but len(gridname_to_grid) != 1")

        self.max_traj_len = max_traj_len
        self.include_velocities = include_velocities
        self.include_accelerations = include_accelerations
        self.include_time = include_time
        self.has_target = has_target
        self.include_grid_name = include_grid_name

        self.word_tokenizer = word_tokenizer

        self._grid_name_to_grid = gridname_to_grid

        self._nearest_kb_label_dict = self._get_nearest_kb_label_dict(gridname_to_grid)

        self.data_list = []
        self._set_data(data_path, gridname_to_grid, kb_tokenizer, self.data_list, total = total)


    def get_nearest_kb_label(self, x, y, grid_name, gridname_to_grid):
        """
        Given coords on a keyboard (x, y) and its grid_name returns the nearest keyboard keys

        By default it uses an array assosiated with grid_name
        that stores the nearest key label for every possible coord pair.

        However sometimes the coords are outside of the keyboard boarders.
        In this case we find the nearest key in a loop.
        """        
        grid = gridname_to_grid[grid_name]
        if x < 0 or x >= grid['width'] or y < 0 or y >= grid['height']:
            return self._get_kb_label_without_map(x, y, grid)
        else:
            return self._nearest_kb_label_dict[grid_name][x, y]
    


    def _get_key_center(self, hitbox: Dict[str, int]) -> Tuple[int, int]:
        x = hitbox['x'] + hitbox['w'] / 2
        y = hitbox['y'] + hitbox['h'] / 2
        return x, y
    

    def _get_kb_label_without_map(self, x, y, grid: dict) -> str:
        """
        Returns label of the nearest key on the keyboard without using a map.
         
        Iterates over all keys and calculates the distance to (x, y) to find the nearest one.
        """
        nearest_kb_label = None
        min_dist = float("inf")
        for key in grid['keys']:
            key_x, key_y = self._get_key_center(key['hitbox'])
            dist = (x - key_x)**2 + (y - key_y)**2
            if dist < min_dist:
                min_dist = dist
                if 'label' in key:
                    nearest_kb_label = key['label']
                elif 'action' in key:
                    nearest_kb_label = key['action']  # tokenizer will covert it to <unk>
                else:
                    raise ValueError("Key has no label or action")
        return nearest_kb_label


    def _get_nearest_kb_label_dict(self, gridname_to_grid: dict) -> Dict[str, np.chararray]:
        """
        Creates a dict that maps grid_name to a map (np.chararray) from coordinate to nearest key label.
        """
        nearest_kb_label_dict = {}
        for grid_name, grid in gridname_to_grid.items():
            nearest_kb_label_dict[grid_name] = self._get_coord_to_kb_label(grid)
        return nearest_kb_label_dict
    

    def _get_coord_to_kb_label(self, grid: dict) -> np.chararray:
        coord_to_kb_label = np.chararray(
            (grid['width'], grid['height']), unicode=True) # 1080 x 640 in our case
        coord_to_kb_label.fill('')

        for key in grid['keys']:
            x_left = key['hitbox']['x']
            x_right = x_left + key['hitbox']['w']
            y_top = key['hitbox']['y']
            y_bottom = y_top + key['hitbox']['h']

            # tokenizer will covert actions to <unk>
            label = key['label'] if 'label' in key else key['action']

            if len(label) > 1:
                print(f"Warning: label '{label}' is substituted with {label[0]}")

            coord_to_kb_label[x_left:x_right, y_top:y_bottom] = label


        for x in range(grid['width']):
            for y in range(grid['height']):
                if coord_to_kb_label[x, y] != '':
                    continue
                coord_to_kb_label[x, y] = self._get_kb_label_without_map(x, y, grid)

        return coord_to_kb_label
            

    def _set_data(self,
                  data_path: str,
                  gridname_to_grid: dict,
                  kb_tokenizer,
                  data_list: list,
                  total: Optional[int] = None):
        with open(data_path, "r", encoding="utf-8") as json_file:
            for line in tqdm(json_file, total = total):
                data_list.append(self._get_data_from_json_line(line, gridname_to_grid, kb_tokenizer))


    def _get_dx_dt(self,
                   X: torch.tensor,
                   T: torch.tensor,
                   len: int) -> List[float]:
        """
        Calculates dx/dt for a list of x coordinates and a list of t coordinates.

        Arguments:
        ----------
        X : torch.tensor
            x (position) coordinates.
        T : torch.tensor
            T[i] = time from the beginning of the swipe corresponding to X[i].
        len : int
            Length of the swipe trajectory. Indexes greater than len are ignored.
        """
        dx_dt = torch.zeros_like(X)
        # dx_dt[1:-1] = (X[2:] - X[:-2]) / (T[2:] - T[:-2])
        dx_dt[1:len-1] = (X[2:len] - X[:len-2]) / (T[2:len] - T[:len-2])

        # Example:
        # x0 x1 x2 x3
        # t0 t1 t2 t3
        # dx_dt[0] = 0
        # dx_dt[1] = (x2 - x0) / (t2 - t0)
        # dx_dt[2] = (x3 - x1) / (t3 - t1)
        # dx_dt[3] = 0


        # if True in torch.isnan(dx_dt):
        #     print(dx_dt)
        #     raise ValueError("dx_dt contains NaNs")

        return dx_dt
    
    def _get_data_from_json_line(self,
                                 line,
                                 gridname_to_grid,
                                 kb_tokenizer) -> Tuple[list, list, list, str]:
        """
        Parses a JSON line and returns a dictionary with data.
        """
        data = json.loads(line)

        X = array.array('h', data['curve']['x'])
        Y = array.array('h', data['curve']['y'])
        T = array.array('h', data['curve']['t'])

        grid_name = data['curve']['grid_name']   

        kb_labels = [self.get_nearest_kb_label(x, y, grid_name, gridname_to_grid) for x, y in zip(X, Y)]
        kb_tokens = [kb_tokenizer.get_token(label) for label in kb_labels]
        kb_tokens += [kb_tokenizer.get_token('<pad>')] * (self.max_traj_len - len(kb_labels))
        kb_tokens = array.array('h', kb_tokens)

        if not self.has_target:
            return X, Y, T, kb_tokens, grid_name
        else:
            word: str = data['word']
            return X, Y, T, kb_tokens, word, grid_name


    def __len__(self):
        return len(self.data_list)
    
    def __getitem__(self, idx):
        if self.has_target:
            X_list, Y_list, T_list, kb_tokens, word, grid_name = self.data_list[idx]
        else:
            X_list, Y_list, T_list, kb_tokens, grid_name = self.data_list[idx]

        X = torch.zeros(self.max_traj_len, dtype=torch.float32)
        Y = torch.zeros(self.max_traj_len, dtype=torch.float32)
        T = torch.zeros(self.max_traj_len, dtype=torch.float32)

        grid = self._grid_name_to_grid[grid_name]

        X[:len(X_list)] = torch.tensor(X_list, dtype=torch.float32) / grid['width']
        Y[:len(Y_list)] = torch.tensor(Y_list, dtype=torch.float32) / grid['height']
        T[:len(T_list)] = torch.tensor(T_list, dtype=torch.float32)

        xyt = torch.cat(
            (
                X.reshape(-1, 1),
                Y.reshape(-1, 1),
            ),
            axis = 1
        )

        if self.include_time:
            xyt = torch.cat(
                (
                    xyt,
                    T.reshape(-1, 1)
                ),
                axis = 1
            )

        traj_len = len(X_list)

        if self.include_velocities:
            dx_dt = self._get_dx_dt(X, T, traj_len)
            dy_dt = self._get_dx_dt(Y, T, traj_len)
            xyt = torch.cat(
                [
                    xyt,
                    dx_dt.reshape(-1, 1),
                    dy_dt.reshape(-1, 1)
                ],
                axis = 1
            )

        if self.include_accelerations:
            d2x_dt2 = self._get_dx_dt(dx_dt, T, traj_len)
            d2y_dt2 = self._get_dx_dt(dy_dt, T, traj_len)
            xyt = torch.cat(
                [
                    xyt,
                    d2x_dt2.reshape(-1, 1),
                    d2y_dt2.reshape(-1, 1)
                ],
                axis = 1
            )

        traj_pad_mask = torch.ones(self.max_traj_len, dtype=torch.bool)
        traj_pad_mask[:len(X_list)] = False


        kb_tokens = torch.tensor(kb_tokens, dtype=torch.int64)

        if self.has_target:
            char_seq, word_mask = self.word_tokenizer.tokenize(word)
            word_mask = word_mask[:-1]

            decoder_in_char_seq = char_seq[:-1]
            decoder_out_char_seq = char_seq[1:]

        
        if not self.has_target:
            decoder_out_char_seq = None
            decoder_in_char_seq = None
            word_mask = None
        
        if self.include_grid_name:
            return (xyt, kb_tokens, decoder_in_char_seq, traj_pad_mask, word_mask), decoder_out_char_seq, grid_name
        
        return (xyt, kb_tokens, decoder_in_char_seq, traj_pad_mask, word_mask), decoder_out_char_seq

In [23]:
def get_grid(grid_name: str, grids_path: str) -> dict:
    with open(grids_path, "r", encoding="utf-8") as f:
        return json.load(f)[grid_name]

In [25]:
sample_data = os.path.join(data_root, "valid__in_train_format__default_only.jsonl")
grid_path =  os.path.join(data_root, "gridname_to_grid.json")
grid_name = "default"

grid = get_grid(grid_name, grid_path)
kb_tokenizer = KeyboardTokenizerv1()
word_tokenizer = CharLevelTokenizerv1(os.path.join(data_root, "voc.txt"))


dataset = NeuroSwipeDatasetv1(
    data_path = sample_data,
    gridname_to_grid= {grid_name: grid},
    kb_tokenizer = kb_tokenizer,
    max_traj_len = 299,
    word_tokenizer = word_tokenizer,
    include_time = False,
    include_velocities = True,
    include_accelerations = True,
    total = 9_416
)

100%|██████████| 9416/9416 [00:02<00:00, 4344.67it/s]


In [26]:
# full train dataset before adding nearest_kb_label:
# ----------------------------------
# 16.2GB RAM (when data stored as torch tensors)
# when stored as lists 17Gb is 61%
# when data stored as python arrays with dtype short: 4.8GB RAM


# Now:
# ----
# 9.3 Gb RAM

In [27]:
i = 40
(xyt, kb_tokens, dec_in_char_seq, traj_pad_mask, word_pad_mask), dec_out_char_seq = dataset[i]
print(xyt.shape, kb_tokens.shape, dec_in_char_seq.shape, traj_pad_mask.shape, word_pad_mask.shape, dec_out_char_seq.shape)

torch.Size([299, 6]) torch.Size([299]) torch.Size([35]) torch.Size([299]) torch.Size([35]) torch.Size([35])


In [28]:
with np.printoptions(threshold=1000000):
    print(dataset._nearest_kb_label_dict['default'])

[['й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й'
  'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й'
  'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й'
  'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й'
  'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й'
  'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й'
  'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й'
  'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й'
  'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й' 'й'
  'й' 'й' 'й' 'й' 'й' 'й' 'й' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф'
  'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф'
  'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф'
  'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф'
  'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 'ф' 

In [29]:
from typing import Callable
import math

import torch
import torch.nn as nn
import torch.nn.functional as F

class SwipeCurveTransformerEncoderv1(nn.Module):
    """
    Transformer-based Curve encoder takes in a sequence of vectors and creates a representation
    of a swipe gesture on a samrtphone keyboard.
    Each vector contains information about finger trajectory at a time step.
    It contains:
    * x coordinate
    * y coordinate
    * Optionally: t
    * Optionally: dx/dt
    * Optionally: dy/dt
    * Optionally: keyboard key that has x and y coordinates within its boundaries
    """

    def __init__(self,
                 input_size: int,
                 d_model: int,
                 dim_feedforward: int,
                 num_layers: int,
                 num_heads_first: int,
                 num_heads_other: int,
                 dropout: float = 0.1,
                 device = None):
        """
        Arguments:
        ----------
        input_size: int
            Size of input vectors.
        d_model: int
            Size of the embeddings (output vectors).
            Should be equal to char embedding size of the decoder.
        dim_feedforward: int
        num_layers: int
            Number of encoder layers including the first layer.

        """
        super().__init__()

        device = device or torch.device('cuda' if torch.cuda.is_available() else 'cpu')

        self.first_encoder_layer = nn.TransformerEncoderLayer(
            input_size, num_heads_first, dim_feedforward, dropout, device=device)
        self.liner = nn.Linear(input_size, d_model, device=device)  # to convert embedding to d_model size
        num_layer_after_first = num_layers - 1
        if num_layer_after_first > 0:
            encoder_layer = nn.TransformerEncoderLayer(
                d_model, num_heads_other, dim_feedforward, dropout, device=device)
            self.transformer_encoder = nn.TransformerEncoder(encoder_layer, num_layers)
        else:
            self.transformer_encoder = None
    

    def forward(self, x, pad_mask: torch.tensor):
        x = self.first_encoder_layer(x, src_key_padding_mask=pad_mask)
        x = self.liner(x)
        if self.transformer_encoder:
            x = self.transformer_encoder(x, src_key_padding_mask=pad_mask)
        return x



class SwipeCurveTransformerDecoderv1(nn.Module):
    """
    Decodes a swipe gesture representation into a sequence of characters.

    Uses decoder transformer with masked attention to prevent the model from cheating.
    """

    def __init__(self,
                 char_emb_size,
                 n_classes,
                 nhead,
                 num_decoder_layers,
                 dim_feedforward,
                 dropout,
                 activation = F.relu,
                 device = None):
        super().__init__()

        device = device or torch.device('cuda' if torch.cuda.is_available() else 'cpu')

        self.decoder_layer = nn.TransformerDecoderLayer(
            char_emb_size, nhead, dim_feedforward, dropout, activation, device = device)
        self.transformer_decoder = nn.TransformerDecoder(self.decoder_layer, num_decoder_layers)
        self.out = nn.Linear(char_emb_size, n_classes, device = device)
        # self.softmax = nn.LogSoftmax(dim=2)
    
    def forward(self, x, memory, tgt_mask, memory_key_padding_mask, tgt_key_padding_mask):
        x = self.transformer_decoder(x,
                                     memory,
                                     tgt_mask=tgt_mask,
                                     memory_key_padding_mask=memory_key_padding_mask,
                                     tgt_key_padding_mask=tgt_key_padding_mask)
        x = self.out(x)
        # x = self.softmax(x)
        return x


class PositionalEncoding(nn.Module):
    def __init__(self, d_model: int, max_len: int, device, dropout: float = 0.0):
        super().__init__()
        self.dropout = nn.Dropout(p=dropout)

        position = torch.arange(max_len).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2) * (-math.log(10000.0) / d_model))
        pe = torch.zeros(max_len, 1, d_model)
        pe[:, 0, 0::2] = torch.sin(position * div_term)
        pe[:, 0, 1::2] = torch.cos(position * div_term)
        pe = pe.to(device=device)
        self.register_buffer('pe', pe)

    def forward(self, x: torch.Tensor) -> torch.Tensor:
        """
        Arguments:
        ----------
        x: Tensor, shape ``[seq_len, batch_size, embedding_dim]``
        """
        x = x + self.pe[:x.size(0)]
        return self.dropout(x)


class SwipeCurveTransformer(nn.Module):
    """
    Seq2seq model. Encodes a sequence of points of a
    swipe-keyboard-typing gesture into a sequence of characters.

    n_output_classes = char_vocab_size - 2 because <pad> and <sos>
    tokens are never predicted.
    """

    def _get_mask(self, max_seq_len: int):
        """
        Returns a mask for the decoder transformer.
        """
        mask = torch.triu(torch.ones(max_seq_len, max_seq_len), diagonal=1)
        mask = mask.masked_fill(mask == 1, float('-inf'))
        return mask

    def __init__(self,
                 n_coord_feats: int,
                 char_emb_size: int,
                 char_vocab_size: int,
                 key_emb_size: int,
                 num_encoder_layers: int,
                 num_decoder_layers: int,
                 dim_feedforward: int,
                 num_heads_encoder_1: int,
                 num_heads_encoder_2: int,
                 num_heads_decoder: int,
                 dropout:float,
                 char_embedding_dropout: float,
                 key_embedding_dropout: float,
                 max_out_seq_len: int,
                 max_curves_seq_len: int,
                 activation: Callable = F.relu,
                 device: str = None):
        super().__init__()

        device = device or torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        self.device = device

        input_feats_size = n_coord_feats + key_emb_size

        d_model = char_emb_size

        self.char_embedding_dropout = nn.Dropout(char_embedding_dropout)
        self.key_embedding_dropout = nn.Dropout(key_embedding_dropout)
        
        self.char_embedding = nn.Embedding(char_vocab_size, char_emb_size, device=device)
        self.key_embedding = nn.Embedding(char_vocab_size, key_emb_size, device=device)

        self.encoder = SwipeCurveTransformerEncoderv1(
            input_feats_size, d_model, dim_feedforward,
            num_encoder_layers, num_heads_encoder_1,
            num_heads_encoder_2, dropout, device=device)
        
        self.char_pos_encoder = PositionalEncoding(
            char_emb_size, max_out_seq_len, device=device)
        
        self.key_pos_encoder = PositionalEncoding(
            key_emb_size, max_curves_seq_len, device=device)
        
        n_classes = char_vocab_size - 2  # <sos> and <pad> are not predicted
        self.decoder = SwipeCurveTransformerDecoderv1(
            char_emb_size, n_classes, num_heads_decoder,
            num_decoder_layers, dim_feedforward, dropout, activation, device=device)

        self.mask = self._get_mask(max_out_seq_len).to(device=device)

    def forward(self, x, kb_tokens, y, x_pad_mask, y_pad_mask):
        kb_k_emb = self.key_embedding(kb_tokens)  # keyboard key
        kb_k_emb = self.key_embedding_dropout(kb_k_emb)
        kb_k_emb = self.key_pos_encoder(kb_k_emb)
        x = torch.cat((x, kb_k_emb), axis = -1)
        x = self.encoder(x, x_pad_mask)
        y = self.char_embedding(y)
        y = self.char_embedding_dropout(y)
        y = self.char_pos_encoder(y)
        y = self.decoder(y, x, self.mask, x_pad_mask, y_pad_mask)
        return y
    
    def apply(self, x, kb_tokens, y, x_pad_mask, y_pad_mask):
        kb_k_emb = self.key_embedding(kb_tokens)  # keyboard key
        kb_k_emb = self.key_embedding_dropout(kb_k_emb)
        kb_k_emb = self.key_pos_encoder(kb_k_emb)
        x = torch.cat((x, kb_k_emb), axis = -1)
        x = self.encoder(x, x_pad_mask)
        y = self.char_embedding(y)
        y = self.char_embedding_dropout(y)
        y = self.char_pos_encoder(y)
        mask = self._get_mask(len(y)).to(device=self.device)
        y = self.decoder(y, x, mask, x_pad_mask, y_pad_mask)
        return y

In [30]:
# def get_mask(max_seq_len: int):
#     """
#     Returns a mask for the decoder transformer.
#     """
#     mask = torch.triu(torch.ones(max_seq_len, max_seq_len), diagonal=1)
#     mask = mask.masked_fill(mask == 1, float('-inf'))
#     return mask

# mask = get_mask(5)
# print(mask)

# >>>
# tensor([[0., -inf, -inf, -inf, -inf],
#         [0., 0., -inf, -inf, -inf],
#         [0., 0., 0., -inf, -inf],
#         [0., 0., 0., 0., -inf],
#         [0., 0., 0., 0., 0.]])

In [31]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [32]:
seq_len = 32
batch_size = 10
in_features = 40



encoder = SwipeCurveTransformerEncoderv1(
    input_size=in_features,
    d_model=128,
    dim_feedforward=128,
    num_layers=1,
    num_heads_first=2,
    num_heads_other=4,
    dropout=0.1,
    device=device)



pad_mask = torch.zeros(batch_size, seq_len, dtype=torch.bool)
# as if each batch contains 22 actual sequnce elements and 10 padding elements
pad_mask[:, 10:] = True
pad_mask = pad_mask.to(device)


encoded = encoder(torch.rand(seq_len, batch_size, in_features).to(device), pad_mask)
torch.set_printoptions(threshold=100_000)

encoded.transpose_(0,1)

if True in torch.isnan(encoded):
    print(encoded)
    raise ValueError("encoded contains NaNs")

In [33]:
curves_seq_len = 20
chars_seq_len = 14
batch_size = 10
char_emb_size = 32
n_classes = 5

decoder = SwipeCurveTransformerDecoderv1(
    char_emb_size=char_emb_size,
    n_classes=n_classes,
    nhead=2,
    num_decoder_layers=2,
    dim_feedforward=128,
    dropout=0.1,
    device = device)

def get_mask(max_seq_len: int):
    """
    Returns a mask for the decoder transformer.
    """
    mask = torch.triu(torch.ones(max_seq_len, max_seq_len), diagonal=1)
    mask = mask.masked_fill(mask == 1, float('-inf'))
    return mask

x = torch.rand(chars_seq_len, batch_size, char_emb_size).to(device)
memory = torch.rand(curves_seq_len, batch_size, char_emb_size).to(device)
tgt_mask = get_mask(chars_seq_len).to(device)
memory_key_padding_mask = torch.zeros(batch_size, curves_seq_len, dtype=torch.bool).to(device)
memory_key_padding_mask[:, 15:] = True
tgt_key_padding_mask = torch.zeros(batch_size, chars_seq_len, dtype=torch.bool).to(device)
tgt_key_padding_mask[:, 10:] = True


decoded = decoder(
    x,
    memory,
    tgt_mask=tgt_mask,
    memory_key_padding_mask=memory_key_padding_mask,
    tgt_key_padding_mask=tgt_key_padding_mask)

if True in torch.isnan(decoded):
    print(decoded)
    # raise ValueError("decoded contains NaNs")

print(decoded.shape)

torch.Size([14, 10, 5])


c:\Users\proshian\AppData\Local\Programs\Python\Python310\lib\site-packages\torch\nn\functional.py:4999: UserWarning: Support for mismatched key_padding_mask and attn_mask is deprecated. Use same type for both instead.
  warnings.warn(


In [34]:
word_char_tokenizer = CharLevelTokenizerv1(os.path.join(data_root, "voc.txt"))

In [35]:
word_char_tokenizer.tokenize("троллейбус")

(tensor([36, 19, 17, 15, 12, 12,  6, 10,  2, 20, 18, 33, 34, 34, 34, 34, 34, 34,
         34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34]),
 tensor([False, False, False, False, False, False, False, False, False, False,
         False, False,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True]))

In [36]:
print(word_char_tokenizer.char_to_idx.keys())

dict_keys(['-', 'а', 'б', 'в', 'г', 'д', 'е', 'ж', 'з', 'и', 'й', 'к', 'л', 'м', 'н', 'о', 'п', 'р', 'с', 'т', 'у', 'ф', 'х', 'ц', 'ч', 'ш', 'щ', 'ъ', 'ы', 'ь', 'э', 'ю', 'я', '<eos>', '<pad>', '<unk>', '<sos>'])


In [37]:
len(word_char_tokenizer.tokenize('информационно-телекоммуникационной')[0])

36

In [38]:
len(word_char_tokenizer.tokenize('информационно')[0])

36

In [39]:
word_char_tokenizer.decode(word_char_tokenizer.tokenize('информационно-телекоммуникационной')[0])

'<sos>информационно-телекоммуникационной<eos>'

In [40]:
word_char_tokenizer.max_word_len - 1

35

In [41]:
def prepare_batch_v1(x, y, device):
    (xyt, kb_tokens, dec_in_char_seq, traj_pad_mask, word_pad_mask), dec_out_char_seq = x, y

    xyt = xyt.transpose_(0, 1).to(device)  # (curves_seq_len, batch_size, n_coord_feats)
    kb_tokens = kb_tokens.transpose_(0, 1).to(device) # (curves_seq_len, batch_size)
    dec_in_char_seq = dec_in_char_seq.transpose_(0, 1).to(device)  # (chars_seq_len - 1, batch_size)
    dec_out_char_seq = dec_out_char_seq.transpose_(0, 1).to(device)  # (chars_seq_len - 1, batch_size)

    traj_pad_mask = traj_pad_mask.to(device)  # (batch_size, curves_seq_len)
    word_pad_mask = word_pad_mask.to(device)  # (batch_size, chars_seq_len - 1)

    return (xyt, kb_tokens, dec_in_char_seq, traj_pad_mask, word_pad_mask), dec_out_char_seq

prepare_batch = prepare_batch_v1

In [42]:
max_out_seq_len = word_char_tokenizer.max_word_len - 1

transformer = SwipeCurveTransformer(
    n_coord_feats=6,
    char_emb_size=128,
    char_vocab_size=len(word_char_tokenizer.char_to_idx),
    key_emb_size=54,
    num_encoder_layers=3,
    num_decoder_layers=3,
    dim_feedforward=128,
    num_heads_encoder_1=4,
    num_heads_encoder_2=4,
    num_heads_decoder=4,
    dropout=0.1,
    char_embedding_dropout=0.1,
    key_embedding_dropout=0.1,
    max_out_seq_len=max_out_seq_len,
    max_curves_seq_len=299,
    device = device)

In [43]:
def cross_entropy_with_reshape(pred, target):
    """
    pred - BatchSize x TargetLen x VocabSize
    target - BatchSize x TargetLen
    """
    pred_flat = pred.view(-1, pred.shape[-1])  # BatchSize*TargetLen x VocabSize
    target_flat = target.reshape(-1)  # BatchSize*TargetLen
    return F.cross_entropy(pred_flat, target_flat, ignore_index=0)

In [44]:
from torch.utils.data import DataLoader

loader = DataLoader(dataset, batch_size=10, shuffle=True)


for x, y in loader:
    x, y = prepare_batch(x, y, device)

    char_seq_pred = transformer(*x)

    cross_entropy_with_reshape(char_seq_pred, y)

    
    break

In [45]:
char_seq_pred.transpose(0,1)[0].shape

if True in torch.isnan(char_seq_pred):
    print(char_seq_pred)

In [46]:
print(char_seq_pred.shape)  # max_word_len - 1, batch_size, char_vocab_size - 2 (omitting <sos> and <pad>)

torch.Size([35, 10, 35])


In [47]:
def lr_scheduler(optimizer):
    return torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer,
                                                      patience=20,
                                                      factor=0.5,
                                                      verbose=True)

In [48]:
def init_random_seed(value=42):
    # random.seed(value)
    np.random.seed(value)
    torch.manual_seed(value)
    torch.cuda.manual_seed(value)
    # torch.backends.cudnn.deterministic = True

In [122]:
import heapq



class BeamGenerator:
    def __init__(self, model, tokenizer, voc_set, device):
        self.model = model
        self.tokenizer = tokenizer
        self.voc_set = voc_set
        self.device = torch.device(device)
        self.model.to(self.device)
        self.eos_token_id = tokenizer.char_to_idx['<eos>']

    def __call__(self,
                 xyt, kb_tokens, traj_pad_mask,
                 max_steps_n=40,  # max tokens in a seq
                 return_hypotheses_n=4,  # n best hypothesis to return
                 beamsize=6,  # n best solutions we store in intermidiate comuptations
                 verbose=True
                 ):
        tokens = [self.tokenizer.char_to_idx['<sos>']]
        initial_length = len(tokens)

        # Partial hypothesis is a heap (stored as a list) of tuples.
        # Each tuple consists of a partial (unfinishedaka intermidiate)
        # hypothesis and it's weight.
        # Weight is a measure of likelihood of the hypothesis.
        # [(w1, hypothesis1), (w2, hypothesis2), ...] 
        partial_hypotheses = [(0, tokens)]
        final_hypotheses = []

        while len(partial_hypotheses) > 0:
            cur_partial_score, cur_partial_hypothesis = heapq.heappop(partial_hypotheses)

            dec_in_char_seq = torch.tensor(cur_partial_hypothesis)
            word_pad_mask = torch.zeros_like(dec_in_char_seq, dtype=torch.bool, device=self.device)
            # dummy_y is any tensor with n_dims = 2 (chars_seq_len - 1, batch_size).
            dummy_y = torch.tensor([[1]])
            x = (xyt, kb_tokens, dec_in_char_seq, traj_pad_mask, word_pad_mask)
            x = (el.unsqueeze(0) for el in x)
            model_input, dummy_y = prepare_batch(x, dummy_y, self.device)

            next_tokens_logits = self.model.apply(*model_input).transpose_(0, 1)[0, -1]
            next_tokens_logproba = F.log_softmax(next_tokens_logits)
            topk_continuations = next_tokens_logproba.topk(beamsize)

            for token_score, token_idx in zip(topk_continuations.values, topk_continuations.indices):
                # Convert tesors to loat and int to avoid memory leakage.
                token_score = float(token_score)
                token_idx = int(token_idx)

                # score - нормализованная разность log_softmax всех токенов.
                # Разность, а не сумма, потому что heapq - мин-куча. 
                old_denorm_score = cur_partial_score * np.sqrt(len(cur_partial_hypothesis))
                new_score = (old_denorm_score - token_score) / np.sqrt(len(cur_partial_hypothesis) + 1)

                new_hypothesis = cur_partial_hypothesis + [token_idx]
                new_item = (new_score, new_hypothesis)

                if token_idx == self.eos_token_id or len(new_hypothesis) - initial_length >= max_steps_n:
                    final_hypotheses.append(new_item)
                else:
                    heapq.heappush(partial_hypotheses, new_item)

            if len(partial_hypotheses) > beamsize:
                partial_hypotheses = heapq.nsmallest(beamsize, partial_hypotheses)
                heapq.heapify(partial_hypotheses)

        final_scores, final_token_lists = zip(*final_hypotheses)
        final_texts = [self.tokenizer.decode(final_token_list) for final_token_list in final_token_lists]
        result = list(zip(final_scores, final_texts))
        result.sort()

        if verbose:
            print(result)

        clean_result = []
        for score, word in result:
            word = word.removeprefix("<sos>").removesuffix("<eos>")
            if word not in self.voc_set:
                continue
            clean_result.append((score, word))
            if len(clean_result) == return_hypotheses_n:
                break
        # result = result[:return_hypotheses_n]

        if verbose:
            print(clean_result)

        return clean_result

In [52]:
class GreedyGenerator:
    def __init__(self, model, tokenizer, device):
        self.model = model
        self.tokenizer = tokenizer
        self.device = torch.device(device)
        self.model.to(self.device)
        self.eos_token_id = tokenizer.char_to_idx['<eos>'] 

    def __call__(self, xyt, kb_tokens, traj_pad_mask, max_steps_n=35):
        tokens = [self.tokenizer.char_to_idx['<sos>']]

        # We don't have to put everything to device because it's done in prepare_batch.

        with torch.no_grad():
            for _ in range(max_steps_n):
                dec_in_char_seq = torch.tensor(tokens).to(self.device)
                word_pad_mask = torch.zeros_like(dec_in_char_seq, dtype=torch.bool, device=self.device)
                # dummy_y is any tensor with n_dims = 2 (chars_seq_len - 1, batch_size).
                dummy_y = torch.tensor([[1]])
                x = [xyt, kb_tokens, dec_in_char_seq, traj_pad_mask, word_pad_mask]
                x = [el.unsqueeze(0) for el in x]
                model_input, dummy_y = prepare_batch(x, dummy_y, self.device)
                best_next_token = self.model.apply(*model_input).transpose_(0, 1)
                best_next_token = best_next_token[0, -1].argmax()  # batch_i = 0, decoder_out_onehot_vector_seq_i = -1 
                if best_next_token == self.eos_token_id:
                    break

                tokens.append(int(best_next_token))
        
        return self.tokenizer.decode(tokens)

In [53]:
# class GreedyGeneratorBatched:
#     def __init__(self, model, tokenizer, device):
#         self.model = model
#         self.tokenizer = tokenizer
#         self.device = torch.device(device)
#         self.model.to(self.device)
#         self.eos_token_id = tokenizer.char_to_idx['<eos>'] 

#     def __call__(self, xyt, kb_tokens, traj_pad_mask, max_steps_n=35):
#         curve_seq_len, batchsize, emb_size = xyt.shape
#         tokens = [[self.tokenizer.char_to_idx['<sos>']] for _ in range(batchsize)]

#         xyt = xyt.to(self.device)
#         kb_tokens = kb_tokens.to(self.device)
#         traj_pad_mask = traj_pad_mask.to(self.device)

#         with torch.no_grad():

#             for _ in range(max_steps_n):
#                 dec_in_char_seq = torch.tensor(tokens).to(self.device)
#                 word_pad_mask = torch.zeros_like(dec_in_char_seq, dtype=torch.bool)
#                 # (seqlen, batchsize) but it's ok to have wrong sizes, what important is n_dims
#                 dummy_y = torch.zeros(1, 1, device = self.device)  
#                 x = (xyt, kb_tokens, dec_in_char_seq, traj_pad_mask, word_pad_mask)
#                 model_input, dummy_y = prepare_batch(x, dummy_y, self.device)
#                 best_next_tokens = self.model.apply(*model_input).transpose_(0, 1)  # seq_len, batch_size
                
#                 best_next_token = best_next_token[0, -1].argmax()
#                 if best_next_token == self.eos_token_id:
#                     break

#                 tokens.append(int(best_next_token))
        
#         return self.tokenizer.decode(tokens)

In [54]:
model = SwipeCurveTransformer(
    n_coord_feats=6,
    char_emb_size=128,
    char_vocab_size=len(word_char_tokenizer.char_to_idx),
    key_emb_size=54,
    num_encoder_layers=3,
    num_decoder_layers=3,
    dim_feedforward=128,
    num_heads_encoder_1=4,
    num_heads_encoder_2=4,
    num_heads_decoder=4,
    dropout=0.1,
    char_embedding_dropout=0.1,
    key_embedding_dropout=0.1,
    max_out_seq_len=max_out_seq_len,
    max_curves_seq_len=299,
    device = device)

In [57]:
model.load_state_dict(
    torch.load(os.path.join("..\\data\\trained_models\\m1",
                            "best_model__2023_11_04__18_31_37__0.02530_default_switch_2.pt"),
               map_location = device))

model = model.eval()

In [58]:
greedy_generator = GreedyGenerator(model, word_char_tokenizer, device)


print("{:<20} {:<20}".format("target", "prediction"))
print("-"*31)

n_examples = 40
for i in range(n_examples):

    (xyt, kb_tokens, dec_in_char_seq, traj_pad_mask, word_pad_mask), target = dataset[i]

    pred = greedy_generator(xyt, kb_tokens, traj_pad_mask)

    # strip работвет только потому что в настоящих словах нет этих символов
    pred = pred.strip("<eos><pad>") 
    target = word_char_tokenizer.decode(target).strip("<eos><pad>")
    print("{:<20} {:<20}".format(target, pred))

target               prediction          
-------------------------------
на                   на                  
все                  все                 
добрый               добрый              
девочка              девочка             
сказала              сказала             
скинь                скинь               
геев                 гееев               
тобой                тобой               
была                 быстра              
да                   да                  
муж                  маж                 
щас                  щас                 
она                  она                 
проблема             проблема            
билайн               билайн              
уже                  уже                 
раньше               раньше              
рам                  нам                 
щас                  щас                 
купил                купил               
ты                   ты                  
зовут                зовут               
ко

In [59]:
grid_name_to_grid_path = os.path.join(data_root, "gridname_to_grid.json")
with open(grid_name_to_grid_path, "r", encoding="utf-8") as f:
    grid_name_to_grid = json.load(f)

test_path = os.path.join(data_root, f"test.jsonl")

kb_tokenizer = KeyboardTokenizerv1()
word_tokenizer = CharLevelTokenizerv1(os.path.join(data_root, "voc.txt"))


test_dataset = NeuroSwipeDatasetv1(
    data_path = test_path,
    gridname_to_grid = grid_name_to_grid,
    kb_tokenizer = kb_tokenizer,
    max_traj_len = 299,
    word_tokenizer = word_tokenizer,
    include_time = False,
    include_velocities = True,
    include_accelerations = True,
    has_target=False,
    has_one_grid_only=False,
    include_grid_name=True,
    total = 10_000
)

100%|██████████| 10000/10000 [00:02<00:00, 3439.97it/s]


In [60]:
from tqdm import tqdm

In [61]:
def model_getter(weights_path):
    model = SwipeCurveTransformer(
    n_coord_feats=6,
    char_emb_size=128,
    char_vocab_size=len(word_char_tokenizer.char_to_idx),
    key_emb_size=54,
    num_encoder_layers=3,
    num_decoder_layers=3,
    dim_feedforward=128,
    num_heads_encoder_1=4,
    num_heads_encoder_2=4,
    num_heads_decoder=4,
    dropout=0.1,
    char_embedding_dropout=0.1,
    key_embedding_dropout=0.1,
    max_out_seq_len=max_out_seq_len,
    max_curves_seq_len=299,
    device = device)

    model.load_state_dict(
        torch.load(weights_path,
                map_location = device))
    
    model = model.eval()

    return model

In [62]:
grid_name_to_model = {
    "default": model_getter(os.path.join("..\\data\\trained_models\\m1",
                                         "best_model__2023_11_03__20_42_24__0.02608_default_switch_1.pt")),
    "extra": model_getter(os.path.join("..\\data\\trained_models\\m1",
                                       "best_model__2023_11_04__11_09_35__0.02623_extra_switch_1.pt"))
}

In [87]:
grid_name_to_greedy_generator_v1 = {
    grid_name: GreedyGenerator(grid_name_to_model[grid_name], word_char_tokenizer, device)
    for grid_name in ("default", "extra")
}

In [78]:
grid_name_to_beam_generator = {
    grid_name: BeamGenerator(grid_name_to_model[grid_name], word_char_tokenizer, device)
    for grid_name in ("default", "extra")
}

In [48]:
# test_default_predictions = []

# for i in tqdm(range(len(test_dataset)), position=0, leave=True):

#     (xyt, kb_tokens, dec_in_char_seq, traj_pad_mask, word_pad_mask), target, grid_name = test_dataset[i]

#     pred = grid_name_to_greedy_generator[grid_name](xyt, kb_tokens, traj_pad_mask)

#     # strip работвет только потому что в настоящих словах нет этих символов
#     pred = pred.removeprefix("<sos>") 
#     test_default_predictions.append(pred)

#     if i > 50:
#         break


In [71]:
def create_submission_greedy(dataset,
                             grid_name_to_greedy_generator,
                             baseline_preds_path, 
                             out_path,
                             vocab_set):
    """
    Creates submission file generating words greedily.

    If prediction is not in the vocabulary 
    """

    if os.path.exists(out_path):
        raise ValueError(f"File {out_path} already exists")
    
    with open(out_path, "w", encoding="utf-8") as f:
        with open(baseline_preds_path, "r", encoding="utf-8") as baseline_f:
            for i, (data, baseline_str) in tqdm(enumerate(zip(dataset, baseline_f)), total=len(dataset)):
                (xyt, kb_tokens, _, traj_pad_mask, _), _, grid_name = data
                pred = grid_name_to_greedy_generator[grid_name](xyt, kb_tokens, traj_pad_mask)
                pred = pred.removeprefix("<sos>") 
                if pred in vocab_set:
                    pred_list = [pred, *baseline_str.split(",")[:-1]]
                    pred_str = ",".join(pred_list)
                    f.write(pred_str + "\n")
                else:
                    f.write(baseline_str)

In [128]:
def create_submission_beam(dataset,
                           grid_name_to_beam_generator,
                           out_path,
                           vocab_set,
                           beamsize):
    """
    Creates submission file generating words greedily.

    If prediction is not in the vocabulary 
    """

    if os.path.exists(out_path):
        raise ValueError(f"File {out_path} already exists")
    
    with open(out_path, "w", encoding="utf-8") as f:
        for i, data in tqdm(enumerate(dataset), total=len(dataset)):
            (xyt, kb_tokens, _, traj_pad_mask, _), _, grid_name = data
            pred_list = grid_name_to_beam_generator[grid_name](
                xyt, kb_tokens, traj_pad_mask, max_steps_n = 35, beamsize=beamsize)
            pred_list = [pred for score, pred in pred_list]
            pred_str = ",".join(pred_list)
            f.write(pred_str + "\n")

In [66]:
def get_vocab_set(vocab_path: str):
    with open(vocab_path, 'r', encoding = "utf-8") as f:
        return set(f.read().splitlines())

In [67]:
vocab_set = get_vocab_set(os.path.join(data_root, "voc.txt"))

In [130]:
grid_name_to_beam_generator = {
    grid_name: BeamGenerator(grid_name_to_model[grid_name], word_char_tokenizer, vocab_set, device)
    for grid_name in ("default", "extra")
}

create_submission_beam(
    test_dataset,
    grid_name_to_beam_generator,
    out_path = "beam_vaaaaaaa.csv",
    vocab_set = vocab_set,
    beamsize = 4
)

  0%|          | 0/10000 [00:00<?, ?it/s]

C:\Users\proshian\AppData\Local\Temp\ipykernel_1704\615880449.py:42: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  next_tokens_logproba = F.log_softmax(next_tokens_logits)
  0%|          | 1/10000 [00:05<15:56:14,  5.74s/it]

[(0.0008783733010204742, '<sos>на<eos>'), (3.1696371289810377, '<sos>неа<eos>'), (3.8569868795402726, '<sos>не<eos>'), (4.091138309639885, '<sos>нас<eos>'), (4.504393394709448, '<sos>наа<eos>'), (4.759143224208373, '<sos>нам<eos>'), (6.565736337814607, '<sos>наса<eos>'), (6.844508035924077, '<sos>нама<eos>'), (7.771531080258702, '<sos>неаа<eos>'), (8.185422199405773, '<sos>наме<eos>'), (9.533563842958248, '<sos>наман<eos>'), (10.326204379373646, '<sos>насан<eos>'), (10.713069025512697, '<sos>намер<eos>'), (10.7204409348716, '<sos>намен<eos>'), (10.823265046642751, '<sos>намана<eos>'), (11.444664567542118, '<sos>насана<eos>'), (11.512987137766036, '<sos>намена<eos>'), (11.518578211520945, '<sos>намера<eos>'), (13.270120165831031, '<sos>наменна<eos>'), (13.355779591263865, '<sos>наменн<eos>'), (14.227538940570716, '<sos>намеран<eos>'), (14.444730435818201, '<sos>наменая<eos>'), (14.44671602493933, '<sos>насанаа<eos>'), (15.265103259142048, '<sos>наменная<eos>'), (15.298843537321233, '<so

  0%|          | 2/10000 [00:13<18:48:15,  6.77s/it]

[(0.000244933299079967, '<sos>что<eos>'), (3.5432364574107953, '<sos>сто<eos>'), (3.8617252521417513, '<sos>чтоб<eos>'), (4.777108238757158, '<sos>чток<eos>'), (4.912972282836323, '<sos>чтом<eos>'), (6.383715821662918, '<sos>со<eos>'), (6.476847843880072, '<sos>стол<eos>'), (6.564216278746244, '<sos>чт<eos>'), (6.611136411920973, '<sos>стои<eos>'), (6.721213641142791, '<sos>чтобы<eos>'), (6.955051450231089, '<sos>стоит<eos>'), (7.45920292360798, '<sos>стоил<eos>'), (7.8066053315997115, '<sos>ст<eos>'), (8.943193987703932, '<sos>сои<eos>'), (9.12811469195712, '<sos>стоито<eos>'), (9.213357914932855, '<sos>стоить<eos>'), (9.274375284749583, '<sos>стоили<eos>'), (9.501500359266258, '<sos>соил<eos>'), (9.634375157845032, '<sos>соит<eos>'), (10.290774741846887, '<sos>соис<eos>'), (10.637533559485494, '<sos>соито<eos>'), (10.978215363834986, '<sos>соили<eos>'), (11.228137907602381, '<sos>стоились<eos>'), (11.36198388269016, '<sos>стоилис<eos>'), (11.511113022343121, '<sos>соист<eos>'), (11.8

...

[(0.3075472257726947, '<sos>вспомнить<eos>'), (0.6802648144839649, '<sos>вспомнил<eos>'), (0.8161951097069666, '<sos>вспомнат<eos>'), (0.9813721020692783, '<sos>вспоминать<eos>'), (0.9871683524064476, '<sos>вспомнилась<eos>'), (1.0239250448834627, '<sos>вспоминат<eos>'), (1.058074124550391, '<sos>вспомнит<eos>'), (1.0605254844408898, '<sos>вспомиграть<eos>'), (1.0819566112506416, '<sos>вспомнать<eos>'), (1.1387076567159635, '<sos>вспомнила<eos>'), (1.6850895676446573, '<sos>вспомни<eos>'), (1.8230962003126563, '<sos>вспомиграт<eos>'), (2.4281149800045982, '<sos>вспомигнать<eos>'), (2.439352936279002, '<sos>вспомигать<eos>'), (2.6548297338034406, '<sos>вспомиграти<eos>'), (2.874934234540846, '<sos>вспомигат<eos>'), (2.886231483144146, '<sos>вспомигнат<eos>'), (3.248924631171907, '<sos>вспомигновать<eos>'), (3.5606084542499254, '<sos>вспомигратить<eos>'), (3.69726468870985, '<sos>вспомигратье<eos>'), (3.880649055856297, '<sos>вспомигновь<eos>'), (3.9087640092421254, '<sos>вспомигратит<eo

  0%|          | 21/10000 [02:27<19:28:13,  7.02s/it]

[(0.5177426019562393, '<sos>максим<eos>'), (0.5333690779128423, '<sos>макапим<eos>'), (0.6143151067195125, '<sos>макаим<eos>'), (0.8185442211882522, '<sos>макамим<eos>'), (1.782684983452782, '<sos>макамис<eos>'), (2.173645630055727, '<sos>маками<eos>'), (2.187409979679311, '<sos>макаими<eos>'), (2.1894336952596323, '<sos>макапими<eos>'), (2.3531151429823827, '<sos>макамимся<eos>'), (2.3737160924233396, '<sos>макапимим<eos>'), (2.406757086630341, '<sos>макаимим<eos>'), (2.5310508880757006, '<sos>макамимс<eos>'), (2.5519075394744095, '<sos>макам<eos>'), (2.9143584974038195, '<sos>макаимис<eos>'), (3.0544679995731174, '<sos>макс<eos>'), (3.408224866663948, '<sos>макси<eos>'), (3.6210558267739823, '<sos>макап<eos>'), (3.978526479962511, '<sos>макаимимся<eos>'), (4.070811932199728, '<sos>макаимими<eos>'), (4.1019722225212485, '<sos>макапимимся<eos>'), (4.139855857329558, '<sos>макаимимс<eos>'), (4.149017325609762, '<sos>макапимимс<eos>'), (4.418942992374802, '<sos>макаимист<eos>'), (4.78398

  0%|          | 21/10000 [02:31<20:03:35,  7.24s/it]


KeyboardInterrupt: 

In [51]:
# from concurrent.futures import ProcessPoolExecutor
# from functools import partial

# def predict_example(data, grid_name_to_greedy_generator):
#     i, ((xyt, kb_tokens, _, traj_pad_mask, _), _, grid_name) = data
#     generator = grid_name_to_greedy_generator[grid_name]
#     pred = generator(xyt, kb_tokens, traj_pad_mask)
#     pred = pred.removeprefix("<sos>")
#     return i, pred

# def get_model_predictions(dataset,
#                           grid_name_to_greedy_generator,
#                           num_workers=2):
#     """
#     Creates submission file generating words greedily.

#     If prediction is not in the vocabulary 
#     """
#     predictions = [None] * len(dataset)
    
#     g2gg = grid_name_to_greedy_generator
    
#     with ProcessPoolExecutor(num_workers) as executor:
#         process_function = partial(predict_example, grid_name_to_greedy_generator=g2gg)
#         for idx, result in tqdm.tqdm(executor.map(process_function, enumerate(dataset)), total=len(dataset)):
#                 predictions[idx] = result
    
#     return predictions

In [52]:
# class ParallelProcessor:
#     def __init__(self, num_workers):
#         self.num_workers = num_workers

#     def process(self, data, process_function, *additional_args):
#         results = [None] * len(data)
#         with ProcessPoolExecutor(max_workers=self.num_workers) as executor: 
#             process_function = partial(process_function, *additional_args)
#             for idx, result in tqdm.tqdm(executor.map(process_function, enumerate(data)), total=len(data)):
#                 results[idx] = result

#         return results

In [53]:
# from multiprocessing import Pool

# def get_model_predictions(dataset, grid_name_to_greedy_generator, num_workers=4):
#     predictions = [None] * len(dataset)
#     g2gg = grid_name_to_greedy_generator

#     with Pool(num_workers) as pool:
#         process_function = partial(predict_example, grid_name_to_greedy_generator=g2gg)
#         for idx, result in tqdm(pool.imap(process_function, enumerate(dataset)), total=len(dataset)):
#             predictions[idx] = result

#     return predictions

In [152]:
# model_preds = get_model_predictions(
#     test_dataset,
#     grid_name_to_greedy_generator_v1,
#     num_workers=2
# )

NameError: name 'get_model_predictions' is not defined

In [74]:
from tqdm import tqdm

The sell below is commented out until i find out if computation results are the same as when we use regular prepare_batch

In [226]:
# def prepare_batch_with_pad_clipping(x, y, device):
#     (xyt, kb_tokens, dec_in_char_seq, traj_pad_mask, word_pad_mask), dec_out_char_seq = x, y

#     max_curve_len = int(torch.max(torch.sum(~traj_pad_mask, dim = 1)))
#     # print(max_curve_len)

#     xyt = xyt[:, :max_curve_len].transpose_(0, 1).to(device)  # (curves_seq_len, batch_size, n_coord_feats)
#     kb_tokens = kb_tokens[:, :max_curve_len].transpose_(0, 1).to(device) # (curves_seq_len, batch_size)
#     dec_in_char_seq = dec_in_char_seq.transpose_(0, 1).to(device)  # (chars_seq_len - 1, batch_size)
#     dec_out_char_seq = dec_out_char_seq.transpose_(0, 1).to(device)  # (chars_seq_len - 1, batch_size)

#     traj_pad_mask = traj_pad_mask[:, :max_curve_len].to(device)  # (batch_size, max_curve_len)
#     # traj_pad_mask = torch.zeros_like(kb_tokens, dtype = torch.bool).transpose_(0, 1).to(device)
#     word_pad_mask = word_pad_mask.to(device)  # (batch_size, chars_seq_len - 1)

#     return (xyt, kb_tokens, dec_in_char_seq, traj_pad_mask, word_pad_mask), dec_out_char_seq

# prepare_batch = prepare_batch_with_pad_clipping

In [73]:
grid_name_to_greedy_generator = {
    grid_name: GreedyGenerator(grid_name_to_model[grid_name], word_char_tokenizer, device)
    for grid_name in ("default", "extra")
}

In [76]:
create_submission_greedy(
    test_dataset,
    grid_name_to_greedy_generator,
    baseline_preds_path = "../data/submissions/sample_submission.csv",
    out_path = "greedy_submionvdrp.csv",
    vocab_set = vocab_set
)

  0%|          | 4/10000 [00:03<2:40:03,  1.04it/s]


KeyboardInterrupt: 

In [ ]:
def remove_duplicates(preds):
    new_preds = []
    met_preds = {}
    for pred in preds:
        if pred in met_preds:
            continue
        met_preds.add(pred)
        new_preds.append(pred)
    return new_preds

def get_metric(submission, ref):
    # Works properly if has duplicates or n_line_preds < 4

    MMR = 0
    with open(submission) as f:
        lines = f.readlines()
        for line, target in zip(lines, ref):
            preds = line.split(",")
            preds = remove_duplicates(preds)

            weights = [1, 0.1, 0.09, 0.08]

            line_MRR = sum(weights[i]*pred for i, pred in enumerate(preds))

            MMR += line_MRR

    return MMR